In [1]:
gameFolder = "DOA++-MAME"

In [2]:
import sys, os
import time
timeDepSeed = int((time.time()-int(time.time()-0.5))*1000)

sys.path.append(os.path.join(os.path.abspath(''), '../'))   
sys.path.append(os.path.join(os.path.abspath(''), '../../../games',gameFolder))   

tensorBoardFolder = "./ppo2_TB_CustCnnLnLstmNoShared/"
modelFolder = "ppo2_Model_CustCnnLnLstmNoShared/"

os.makedirs(modelFolder, exist_ok=True)

In [3]:
from makeDiambraEnv import *

import tensorflow as tf

from customPolicies.customCnnLstmPolicyNoShared import *

from stable_baselines import PPO2
from stable_baselines.common.evaluation import evaluate_policy
from stable_baselines.common.callbacks import BaseCallback

In [4]:
class AutoSave(BaseCallback):
    """
    Callback for saving a model (the check is done every ``check_freq`` steps)

    :param check_freq: (int)
    :param save_path: (str) Path to the folder where the model will be saved.
    :param verbose: (int)
    """
    def __init__(self, check_freq: int, save_path: str, verbose=1):
        super(AutoSave, self).__init__(verbose)
        self.check_freq = check_freq
        self.save_path_base = save_path + 'autoSave_'

    def _on_step(self) -> bool:
        if self.n_calls % self.check_freq == 0:
            # Example for saving best model
            if self.verbose > 0:
                print("Saving new best model to {}".format(self.save_path_base))
            # Save the agent
            self.model.save(self.save_path_base+str(self.n_calls)+"steps_action+_add")

        return True

In [5]:
diambraKwargs = {}
diambraKwargs["roms_path"] = "../../../roms/MAMEToolkit/roms/"
diambraKwargs["binary_path"] = "../../../../customMAME/"
diambraKwargs["player"] = "P1"
diambraKwargs["frame_ratio"] = 3
diambraKwargs["render"] = False
#diambraKwargs["throttle"] = False
#diambraKwargs["sound"] = False 
#diambraKwargs["character"] ="Random"
diambraKwargs["character"] = "Kasumi"

wrapperKwargs = {}
wrapperKwargs["frame_stack"] = 1
wrapperKwargs["clip_rewards"] = False
wrapperKwargs["normalize_rewards"] = True
wrapperKwargs["scale"] = True
wrapperKwargs["scale_mod"] = 0
wrapperKwargs["hwc_obs_resize"] = [256, 256, 1]

#keyToAdd = None
keyToAdd = []
keyToAdd.append("actionsBuf")
#keyToAdd.append("player")
keyToAdd.append("healthP1")
keyToAdd.append("healthP2")
keyToAdd.append("positionP1")
keyToAdd.append("positionP2")
#keyToAdd.append("winsP1")
#keyToAdd.append("winsP2")

numEnv=1

env = make_diambra_env(diambraMame, env_prefix="Train", num_env=numEnv, seed=timeDepSeed, 
                       continue_game = -2, diambra_kwargs = diambraKwargs, 
                       wrapper_kwargs = wrapperKwargs, key_to_add = keyToAdd)

# OR 
#env = make_diambra_env(diambraMame, num_env=2, seed=0, diambra_kwargs = diambraKwargs)
# Frame-stacking with 4 frames
#env = VecFrameStack(env, n_stack=4)


Env_id =  Train0
Continue value =  -2
Player = P1 , Character = Kasumi
Noop action N =  11


In [ ]:
print("Obs_space = ", env.observation_space)
print("Obs_space type = ", env.observation_space.dtype)
print("Obs_space high = ", env.observation_space.high)
print("Obs_space low = ", env.observation_space.low)

In [ ]:
print("Act_space = ", env.action_space)
print("Act_space type = ", env.action_space.dtype)
print("Act_space n = ", env.action_space.n)

In [6]:
# Policy arguments
policyKwargs={}
#policyKwargs["scale_in"] = False
policyKwargs["n_add_info"] = 148
policyKwargs["layers"] = [128, 64]
policyKwargs["layers_policy"] = [64, 64]
policyKwargs["layers_value"] = [64, 64]

# Model arguments to override load
customObjects={}
customObjects["learning_rate"]=5e-5 # Changed from 2.5e-4 to 5e-5 @ ~6.6M iter

# Initialize the model, 1 env
#model = PPO2(CustomCnnLstmPolicyNoShared, env, nminibatches=numEnv, verbose=1,
#             tensorboard_log=tensorBoardFolder, policy_kwargs=policyKwargs, gamma = 0.94)

#OR

# Load the trained agent, 1 env
model = PPO2.load(modelFolder+"7_3Msteps_action+_add", env=env, custom_objects=customObjects,
                  tensorboard_log=tensorBoardFolder, 
                  policy_kwargs=policyKwargs, gamma = 0.94)





Instructions for updating:
Use keras.layers.flatten instead.

Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where




In [7]:
print(model.learning_rate)

5e-05


In [ ]:
# Create the callback: autosave every 100000 steps
autoSaveCallback = AutoSave(check_freq=100000, save_path=modelFolder+"7_3M_")

# Train the agent
time_steps = 10000000
model.learn(total_timesteps=time_steps, callback=autoSaveCallback)


Setting difficulty = 3
Starting game
Selecting Kasumi
Waiting for fight to start
-------------------------------------
| approxkl           | 0.014020277  |
| clipfrac           | 0.111328125  |
| explained_variance | -0.0951      |
| fps                | 2            |
| n_updates          | 1            |
| policy_entropy     | 0.87106955   |
| policy_loss        | -0.030774621 |
| serial_timesteps   | 128          |
| time_elapsed       | 2.07e-05     |
| total_timesteps    | 128          |
| value_loss         | 0.003143904  |
-------------------------------------
Round done
-------------------------------------
| approxkl           | 0.0056424476 |
| clipfrac           | 0.064453125  |
| explained_variance | -0.00962     |
| fps                | 12           |
| n_updates          | 2            |
| policy_entropy     | 0.8196049    |
| policy_loss        | -0.019894198 |
| serial_timesteps   | 256          |
| time_elapsed       | 55.4         |
| total_timesteps    | 256       

-------------------------------------
| approxkl           | 0.00388608   |
| clipfrac           | 0.02734375   |
| explained_variance | -0.00822     |
| fps                | 25           |
| n_updates          | 17           |
| policy_entropy     | 0.8251836    |
| policy_loss        | -0.012077706 |
| serial_timesteps   | 2176         |
| time_elapsed       | 163          |
| total_timesteps    | 2176         |
| value_loss         | 0.0075103017 |
-------------------------------------
Round done
-------------------------------------
| approxkl           | 0.0027746346 |
| clipfrac           | 0.02734375   |
| explained_variance | 0.0154       |
| fps                | 12           |
| n_updates          | 18           |
| policy_entropy     | 0.7792915    |
| policy_loss        | -0.0123927   |
| serial_timesteps   | 2304         |
| time_elapsed       | 168          |
| total_timesteps    | 2304         |
| value_loss         | 0.007939218  |
-------------------------------------
-

--------------------------------------
| approxkl           | 0.0027476363  |
| clipfrac           | 0.033203125   |
| explained_variance | -0.0137       |
| fps                | 27            |
| n_updates          | 34            |
| policy_entropy     | 0.71400905    |
| policy_loss        | -0.0096666105 |
| serial_timesteps   | 4352          |
| time_elapsed       | 279           |
| total_timesteps    | 4352          |
| value_loss         | 0.0060634366  |
--------------------------------------
-------------------------------------
| approxkl           | 0.004147606  |
| clipfrac           | 0.0390625    |
| explained_variance | -0.00482     |
| fps                | 27           |
| n_updates          | 35           |
| policy_entropy     | 0.74890614   |
| policy_loss        | -0.01167333  |
| serial_timesteps   | 4480         |
| time_elapsed       | 284          |
| total_timesteps    | 4480         |
| value_loss         | 0.0007426393 |
-------------------------------------

Round done
-------------------------------------
| approxkl           | 0.00614805   |
| clipfrac           | 0.029296875  |
| explained_variance | 0.00119      |
| fps                | 11           |
| n_updates          | 51           |
| policy_entropy     | 0.75549024   |
| policy_loss        | -0.014980568 |
| serial_timesteps   | 6528         |
| time_elapsed       | 399          |
| total_timesteps    | 6528         |
| value_loss         | 0.0053273104 |
-------------------------------------
-------------------------------------
| approxkl           | 0.012319231  |
| clipfrac           | 0.052734375  |
| explained_variance | 0.0141       |
| fps                | 26           |
| n_updates          | 52           |
| policy_entropy     | 0.8120776    |
| policy_loss        | -0.013992764 |
| serial_timesteps   | 6656         |
| time_elapsed       | 410          |
| total_timesteps    | 6656         |
| value_loss         | 0.005836328  |
-------------------------------------
-

-------------------------------------
| approxkl           | 0.00554495   |
| clipfrac           | 0.03125      |
| ep_len_mean        | 7.21e+03     |
| ep_reward_mean     | -0.298       |
| explained_variance | 0.00505      |
| fps                | 27           |
| n_updates          | 66           |
| policy_entropy     | 0.7290031    |
| policy_loss        | -0.009691659 |
| serial_timesteps   | 8448         |
| time_elapsed       | 508          |
| total_timesteps    | 8448         |
| value_loss         | 0.007041021  |
-------------------------------------
Stage done
--------------------------------------
| approxkl           | 0.0027479616  |
| clipfrac           | 0.033203125   |
| ep_len_mean        | 7.21e+03      |
| ep_reward_mean     | -0.298        |
| explained_variance | 0.0127        |
| fps                | 10            |
| n_updates          | 67            |
| policy_entropy     | 0.7497877     |
| policy_loss        | -0.0123695135 |
| serial_timesteps   | 8576  

...

Episode done
Restarting game
Selecting Kasumi
Waiting for fight to start
-------------------------------------
| approxkl           | 0.009196726  |
| clipfrac           | 0.06640625   |
| ep_len_mean        | 6.24e+03     |
| ep_reward_mean     | 3.39         |
| explained_variance | 0.0511       |
| fps                | 10           |
| n_updates          | 8176         |
| policy_entropy     | 0.91421443   |
| policy_loss        | -0.02261351  |
| serial_timesteps   | 1046528      |
| time_elapsed       | 5.47e+04     |
| total_timesteps    | 1046528      |
| value_loss         | 0.0047172895 |
-------------------------------------
-------------------------------------
| approxkl           | 0.007807998  |
| clipfrac           | 0.05859375   |
| ep_len_mean        | 6.24e+03     |
| ep_reward_mean     | 3.39         |
| explained_variance | 0.0375       |
| fps                | 29           |
| n_updates          | 8177         |
| policy_entropy     | 0.868997     |
| policy_loss  

-------------------------------------
| approxkl           | 0.0018280896 |
| clipfrac           | 0.025390625  |
| ep_len_mean        | 6.24e+03     |
| ep_reward_mean     | 3.39         |
| explained_variance | 0.00998      |
| fps                | 29           |
| n_updates          | 8191         |
| policy_entropy     | 0.9755211    |
| policy_loss        | -0.012817655 |
| serial_timesteps   | 1048448      |
| time_elapsed       | 5.48e+04     |
| total_timesteps    | 1048448      |
| value_loss         | 0.011177675  |
-------------------------------------
-------------------------------------
| approxkl           | 0.007059073  |
| clipfrac           | 0.01953125   |
| ep_len_mean        | 6.24e+03     |
| ep_reward_mean     | 3.39         |
| explained_variance | 0.0117       |
| fps                | 29           |
| n_updates          | 8192         |
| policy_entropy     | 0.9446807    |
| policy_loss        | -0.0126647   |
| serial_timesteps   | 1048576      |
| time_elaps

--------------------------------------
| approxkl           | 0.0018032035  |
| clipfrac           | 0.025390625   |
| ep_len_mean        | 6.24e+03      |
| ep_reward_mean     | 3.39          |
| explained_variance | 0.00356       |
| fps                | 28            |
| n_updates          | 8206          |
| policy_entropy     | 0.8996762     |
| policy_loss        | -0.0089966245 |
| serial_timesteps   | 1050368       |
| time_elapsed       | 5.49e+04      |
| total_timesteps    | 1050368       |
| value_loss         | 0.0055891946  |
--------------------------------------
-------------------------------------
| approxkl           | 0.007100799  |
| clipfrac           | 0.044921875  |
| ep_len_mean        | 6.24e+03     |
| ep_reward_mean     | 3.39         |
| explained_variance | 0.00091      |
| fps                | 29           |
| n_updates          | 8207         |
| policy_entropy     | 0.95121896   |
| policy_loss        | -0.016829416 |
| serial_timesteps   | 1050496     

-------------------------------------
| approxkl           | 0.004819076  |
| clipfrac           | 0.04296875   |
| ep_len_mean        | 6.24e+03     |
| ep_reward_mean     | 3.39         |
| explained_variance | 0.000731     |
| fps                | 29           |
| n_updates          | 8221         |
| policy_entropy     | 0.95230824   |
| policy_loss        | -0.018166749 |
| serial_timesteps   | 1052288      |
| time_elapsed       | 5.5e+04      |
| total_timesteps    | 1052288      |
| value_loss         | 0.008690067  |
-------------------------------------
Round done
-------------------------------------
| approxkl           | 0.008883275  |
| clipfrac           | 0.0234375    |
| ep_len_mean        | 6.24e+03     |
| ep_reward_mean     | 3.39         |
| explained_variance | 0.0105       |
| fps                | 13           |
| n_updates          | 8222         |
| policy_entropy     | 0.87584734   |
| policy_loss        | -0.010822151 |
| serial_timesteps   | 1052416      |
|

-------------------------------------
| approxkl           | 0.0034293858 |
| clipfrac           | 0.033203125  |
| ep_len_mean        | 6.25e+03     |
| ep_reward_mean     | 3.36         |
| explained_variance | -0.0318      |
| fps                | 29           |
| n_updates          | 8236         |
| policy_entropy     | 0.9179392    |
| policy_loss        | -0.013406061 |
| serial_timesteps   | 1054208      |
| time_elapsed       | 5.51e+04     |
| total_timesteps    | 1054208      |
| value_loss         | 0.008294155  |
-------------------------------------
-------------------------------------
| approxkl           | 0.002650855  |
| clipfrac           | 0.0234375    |
| ep_len_mean        | 6.25e+03     |
| ep_reward_mean     | 3.36         |
| explained_variance | -0.00304     |
| fps                | 29           |
| n_updates          | 8237         |
| policy_entropy     | 0.9541286    |
| policy_loss        | -0.011327162 |
| serial_timesteps   | 1054336      |
| time_elaps

In [ ]:
# Save the agent
model.save(modelFolder+"6_6Msteps_action+_add")

In [ ]:
observation = env.reset()
states = None

while True:

    action, states = model.predict(observation, states, deterministic=False)
    action_prob = model.action_probability(observation, states)
    #print("Action probabilities = ", action_prob)
    #print("Max action = ", np.argmax(action_prob))
    #print("Action = ", action)
    #input("Pausa")
    
    observation, reward, done, info = env.step(action)
    if done:
        observation = env.reset()
        states = None
        
env.close()

In [ ]:
observation = env.reset()
states = None

cumulativeEpRew = 0.0
cumulativeEpRewAll = []
cumulativeTotRew = 0.0

maxNumEp = 100
currNumEp = 0

while currNumEp < maxNumEp:

    action, states = model.predict(observation, states, deterministic=False)
    action_prob = model.action_probability(observation, states)
    #print("Action probabilities = ", action_prob)
    #print("Max action = ", np.argmax(action_prob))
    #print("Action = ", action)
    
    observation, reward, done, info = env.step(action)
    
    cumulativeEpRew += reward
    
    if np.any(done):
        currNumEp += 1
        print("Ep. # = ", currNumEp)
        print("Ep. Cumulative Rew # = ", cumulativeEpRew)
        sys.stdout.flush()
        cumulativeEpRewAll.append(cumulativeEpRew)
        cumulativeTotRew += cumulativeEpRew
        cumulativeEpRew = 0.0

        observation = env.reset()
        states = None

print("Mean cumulative reward = ", cumulativeTotRew/maxNumEp)    
print("Mean cumulative reward = ", np.mean(cumulativeEpRewAll))    
print("Std cumulative reward = ", np.std(cumulativeEpRewAll))   
    
env.close()